# Kaggle Animal Shelter Results

The following report gives the results from the Kaggle Animal Shelter Competition.

## Project Description

The goal of this project is to predict the outcome of animals as they leave a shelter in Austin, Texas.  The outcome for each animal is one of the following: Adoption, Died, Euthanasia, Return to Owner or Transfer. We are given a train set and test set.  The test set does not include outcome labels and is used for competition leaderboard scoring.  This analysis uses only the train set which has labels.


In [1]:
# Import modules

import pandas as pd
import numpy as np
import os
import sys
import random
import copy
import cPickle as pickle
import datetime

import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
import colorlover as cl
import matplotlib.pyplot as plt 

src_dir = os.path.join(os.getcwd(), os.pardir)
sys.path.append(src_dir)

from sklearn.model_selection import ShuffleSplit
from scipy.stats import spearmanr
from scipy import stats
from sklearn import decomposition
from sklearn.preprocessing import StandardScaler
from scipy.stats import boxcox
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error

import src.plotting_methods as pm
#import imp
#pm = imp.load_source('pm', '/Volumes/Work/Projects/Kaggle_Animal_Shelter/src/plotting_methods.py')

init_notebook_mode(connected=True)

%reload_ext autoreload
%autoreload 2

pd.options.display.float_format = '{:,.4f}'.format

In [3]:
# Load data

#raw_data_dir = 'C:\Users\Colleen\Documents\Kaggle_Animal_Shelter\data'
raw_data_dir = '/Volumes/Work/Projects/Kaggle_Animal_Shelter/data'

f = open(os.path.join(raw_data_dir, 'train.csv'), 'r')
train_data = pd.read_csv(f)
f.close()


## Data Cleaning and Exploration

The data set has the following size:

In [50]:
print 'Number of samples: ' + str(train_data.shape[0])
print 'Number of columns: ' + str(train_data.shape[1])

Number of samples: 26729
Number of columns: 10


The columns, their types and number of unique values are shown below, along with the first few rows of the data

In [54]:
df = pd.concat([train_data.dtypes, train_data.apply(lambda x: len(np.unique(x)))], 1)
df.columns = ['type', 'num_unique_vals']
df

type  num_unique_vals
AnimalID        object            26729
Name            object            14065
DateTime        object            22918
OutcomeType     object                5
OutcomeSubtype  object            13628
AnimalType      object                2
SexuponOutcome  object                6
AgeuponOutcome  object               62
Breed           object             1380
Color           object              366

In [55]:
train_data.head()

AnimalID     Name             DateTime      OutcomeType OutcomeSubtype  \
0  A671945  Hambone  2014-02-12 18:22:00  Return_to_owner            NaN   
1  A656520    Emily  2013-10-13 12:44:00       Euthanasia      Suffering   
2  A686464   Pearce  2015-01-31 12:28:00         Adoption         Foster   
3  A683430      NaN  2014-07-11 19:09:00         Transfer        Partner   
4  A667013      NaN  2013-11-15 12:52:00         Transfer        Partner   

  AnimalType SexuponOutcome AgeuponOutcome                        Breed  \
0        Dog  Neutered Male         1 year        Shetland Sheepdog Mix   
1        Cat  Spayed Female         1 year       Domestic Shorthair Mix   
2        Dog  Neutered Male        2 years                 Pit Bull Mix   
3        Cat    Intact Male        3 weeks       Domestic Shorthair Mix   
4        Dog  Neutered Male        2 years  Lhasa Apso/Miniature Poodle   

         Color  
0  Brown/White  
1  Cream Tabby  
2   Blue/White  
3   Blue Cream  
4          Tan

We can ignore 'AnimalID' since its just a unique identify for each animal. The 'OutcomeType' is our target variable.  The features appear to all be string types.

This is clearly a multi-class classification problem with mostly categorical variables. Some of these variables have large number of categories which we will need to reduce.  Also there are some missing values we need to deal with.

We will go through each variable and do some cleaning and transformations into usable features. We need to use the full data set in order to capture all the categories for each variable.  However, we'll only do some basic exploration to avoid biasing our results.

### DateTime

These are strings, so we convert them to datetime objects.  We print the first few values and plot the distribution of times.

In [4]:
train_data['DateTime'].head()

0    2014-02-12 18:22:00
1    2013-10-13 12:44:00
2    2015-01-31 12:28:00
3    2014-07-11 19:09:00
4    2013-11-15 12:52:00
Name: DateTime, dtype: object

In [56]:
times = [datetime.datetime.strptime(x, '%Y-%m-%d %H:%M:%S') for x in train_data['DateTime']]

In [57]:
iplot([go.Histogram(x = times)])

There doesn't seem to be any outliers or weird values, and the date range agrees with what's given in the competition description. In addition there appears to be spikes in events in the summer, which we'll investigate later.

### OutcomeType

This is the target variable. We print the counts for each level.

In [41]:
train_data['OutcomeType'].groupby(train_data['OutcomeType']).count().append(pd.Series({'nan': len(train_data['OutcomeType']) - train_data['OutcomeType'].count()}))

Adoption           10769
Died                 197
Euthanasia          1555
Return_to_owner     4786
Transfer            9422
nan                    0
dtype: int64

Right away we can see the target variable is unbalanced.  This means we shouldn't use accuracy when assessing models - we'll use F1 score and look at precision vs recall.

### OutcomeSubtype

This is the subtype of the outcome, further describing what happened to each animal.  We print the counts for each level.

In [40]:
train_data['OutcomeSubtype'].groupby(train_data['OutcomeSubtype']).count().append(pd.Series({'nan': len(train_data['OutcomeSubtype']) - train_data['OutcomeSubtype'].count()}))

Aggressive               320
At Vet                     4
Barn                       2
Behavior                  86
Court/Investigation        6
Enroute                    8
Foster                  1800
In Foster                 52
In Kennel                114
In Surgery                 3
Medical                   66
Offsite                  165
Partner                 7816
Rabies Risk               74
SCRP                    1599
Suffering               1002
nan                    13612
dtype: int64

Thre are many missing values and some categories with very few samples.  We may be able to merge some of these categories.  But we'll leave it for now. 

### AnimalType

This one is categorical and simple - cat or dog. The following are the counts. Its approximately an even split between the animals.

In [42]:
train_data['AnimalType'].groupby(train_data['AnimalType']).count().append(pd.Series({'nan': len(train_data['AnimalType']) - train_data['AnimalType'].count()}))

Cat    11134
Dog    15595
nan        0
dtype: int64

### SexuponOutcome

This one is also categorical, indicating spayed/neutered status and sex of the animal.  These are the counts.  

In [43]:
train_data['SexuponOutcome'].groupby(train_data['SexuponOutcome']).count().append(pd.Series({'nan': len(train_data['SexuponOutcome']) - train_data['SexuponOutcome'].count()}))

Intact Female    3511
Intact Male      3525
Neutered Male    9779
Spayed Female    8820
Unknown          1093
nan                 1
dtype: int64

We'll change the 'Unknown' values to just missing.  It also makes sense to split this into two variables: Sex and IsFixed since, intuitively, sex could affect the outcome of the animal: Some people may prefer one sex to another for adoption, and male and female animals are subject to different health problems.  Also the fixed status could affect outcome, such as people being less likely to adopt intact animals due to aggression.  However doing this would remove interaction effects between Sex and IsFixed, so we may add these effects back in later.

In [15]:
sex = [int('Female' in x) if isinstance(x, str) else np.nan for x in train_data['SexuponOutcome']]
is_fixed = [int('Intact' not in x) if isinstance(x, str) else np.nan for x in train_data['SexuponOutcome']]

### AgeuponOutcome 

These are the unique values:

In [8]:
np.unique(train_data['AgeuponOutcome'])

array([nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
       nan, nan, nan, nan, nan, '0 years', '1 day', '1 month', '1 week',
       '1 weeks', '1 year', '10 months', '10 years', '11 months',
       '11 years', '12 years', '13 years', '14 years', '15 years',
       '16 years', '17 years', '18 years', '19 years', '2 days',
       '2 months', '2 weeks', '2 years', '20 years', '3 days', '3 months',
       '3 weeks', '3 years', '4 days', '4 months', '4 weeks', '4 years',
       '5 days', '5 months', '5 weeks', '5 years', '6 days', '6 months',
       '6 years', '7 months', '7 years', '8 months', '8 years',
       '9 months', '9 years'], dtype=object)

Since age is typically nominal, we can convert these into numbers.  The smallest unit of measure here is days so we'll convert these all to days and plot the histogram.

In [5]:
def get_age(s):
    
    if (s == 'nan') or (isinstance(s, float) and np.isnan(s)):
        return s
    
    n = s.split(' ')
    num = int(n[0])
    time = n[1]
    if num == 0:
        return 0
    elif 'year' in time:
        return num * 365
    elif 'month' in time:
        return num * 30
    else:
        return num

In [6]:
ages = [get_age(s) for s in train_data['AgeuponOutcome']]

In [58]:
iplot([go.Histogram(x = ages)])

This data has an odd distribution - the smaller the age, the more resolution there is.  This makes sense since the age of young animals tend to be measures with high resolution (i.e days and weeks), where as the ages of older animals are typically in years.  In addtion, the age of many of these animals is likely estimated so naturally they'd be heavily binned. (e.g. 1 year, 5 years, 20 years) We'll leave this for now but we may come back to this variable.

## Breed

The number of breeds was very high, around 1300.  The following are the counts and unique values:

In [62]:
x = 'Breed'
cnts = train_data[x].groupby(train_data[x]).count().append(pd.Series({'nan': len(train_data[x]) - train_data[x].count()}))

In [68]:
cnts.sort_values()

nan                                                   0
Newfoundland/Queensland Heeler                        1
Newfoundland/Great Pyrenees                           1
Newfoundland/Border Collie                            1
Newfoundland/Australian Cattle Dog                    1
Chinese Crested/Chihuahua Longhair                    1
Chinese Crested/Papillon                              1
Munchkin Longhair Mix                                 1
Miniature Schnauzer/Whippet                           1
Chihuahua Shorthair/Smooth Fox Terrier                1
Chinese Sharpei/Airedale Terrier                      1
Chinese Sharpei/Basset Hound                          1
Miniature Schnauzer/West Highland                     1
Chinese Sharpei/Great Dane                            1
Miniature Schnauzer/Soft Coated Wheaten Terrier       1
Chinese Sharpei/Pit Bull                              1
Miniature Schnauzer/Shih Tzu                          1
Miniature Schnauzer/Scottish Terrier            

Further investigation shows that the breed names can have the following formats:
    
1. A single breed. E.g. Beagle
2. A combo of two breeds. E.g. Chihuahua Shorthair/Finnish Spitz
3. A combo of three breeds. E.g. Labrador Retriever/Black/Tan Hound
4. Some mix involving a breed. E.g. Pit Bull Mix (unsure if the given breed is the dominant one in the mix or based on some other identification)


Given the high number of categories, and many categories having only 1 member, we should compress these.  We'll turn this into multi-categories by splitting the given breed names into their components - single breeds and the mix identifier. Thus each animal will be assigned 1 to 3 categories of breeds.

E.g. Labrador Retriever/Black/Tan Hound will be assigned the following categories: Labrador Retriever, Black and Tan Hound

E.g. Pit Bull Mix is assigned: Pit Bull and Mix.

This method has the following effects:

1. Eliminates interaction effects between breeds. However, we can add those back in and in a more targeted fashion (i.e. only the interactions which improve classification)
2. Assumes that 'Mix' is a category in itself. We can investigate this effect later
3. Assumes that order of breed doesn't matter. (E.g. 'Black/Tan Hound is same as 'Tan Hound/Black') We can also investigate this.

For now we'll use this method and investigate in more detail later.

In [60]:
from itertools import chain
breeds = np.unique(list(chain.from_iterable([x.split('/') for x in train_data['Breed']])))
breed_cnts = dict([(x, sum([x in y for y in train_data['Breed']])) for x in breeds])

new_breeds = list(np.unique([x.split(' Mix')[0] for x in breeds]))
new_breeds.append('Mix')
new_breed_cnts = dict([(x, sum([x in y for y in train_data['Breed']])) for x in new_breeds])

We now have this number of breed categories:

In [61]:
len(new_breed_cnts)

226

In [9]:
def get_breed_cat(x):
    n = x.split('/')
    
    cats = []
    for y in n:
        n2 = y.split(' Mix')
        if len(n2) == 2:
            n2[1] = 'Mix'
        cats.extend(n2)
    return cats

In [10]:
breed_cats = [get_breed_cat(x) for x in train_data['Breed']]

## Color

There are a lot of these.  They also need to be compressed.

In [74]:
x = 'Color'
cnts = train_data[x].groupby(train_data[x]).count().append(pd.Series({'nan': len(train_data[x]) - train_data[x].count()}))
cnts.sort_values()

nan                               0
Chocolate/Gold                    1
Chocolate/Gray                    1
Chocolate/Red Tick                1
Cream/Orange                      1
Cream/Red                         1
Cream/Red Tick                    1
Cream/Seal Point                  1
Fawn/Brown                        1
Chocolate/Cream                   1
Fawn/Brown Brindle                1
Fawn/Tricolor                     1
Gold/Black                        1
Gold/Buff                         1
Gold/Tan                          1
Gold/Yellow                       1
Gray Tabby/Black                  1
Gray/Red                          1
Liver Tick/White                  1
Yellow/Yellow                     1
Chocolate/Brown Merle             1
Chocolate/Brown Brindle           1
Calico/Orange Tabby               1
Brown Brindle/Blue Tick           1
Brown Brindle/Brown Brindle       1
Brown Brindle/Brown Merle         1
Brown Merle/Blue Merle            1
Brown Merle/Tan             

First we'll get a list of all the colors, by separating the combos

In [11]:
from itertools import chain
colors = np.unique(list(chain.from_iterable([x.split('/') for x in train_data['Color']])))

In [91]:
color_cnts = dict([(x, sum([x in y for y in train_data['Color']])) for x in colors])

In [106]:
len(color_cnts)

57

In [92]:
color_cnts

{'Agouti': 2,
 'Apricot': 30,
 'Black': 8024,
 'Black Brindle': 114,
 'Black Smoke': 69,
 'Black Tabby': 67,
 'Black Tiger': 2,
 'Blue': 2354,
 'Blue Cream': 34,
 'Blue Merle': 181,
 'Blue Point': 31,
 'Blue Smoke': 6,
 'Blue Tabby': 696,
 'Blue Tick': 54,
 'Blue Tiger': 9,
 'Brown': 6693,
 'Brown Brindle': 867,
 'Brown Merle': 84,
 'Brown Tabby': 2696,
 'Brown Tiger': 5,
 'Buff': 328,
 'Calico': 583,
 'Calico Point': 27,
 'Chocolate': 519,
 'Chocolate Point': 24,
 'Cream': 612,
 'Cream Tabby': 282,
 'Fawn': 209,
 'Flame Point': 86,
 'Gold': 84,
 'Gray': 407,
 'Gray Tabby': 55,
 'Lilac Point': 39,
 'Liver': 31,
 'Liver Tick': 4,
 'Lynx Point': 188,
 'Orange': 1438,
 'Orange Tabby': 1353,
 'Orange Tiger': 1,
 'Pink': 4,
 'Red': 985,
 'Red Merle': 59,
 'Red Tick': 59,
 'Ruddy': 1,
 'Sable': 324,
 'Seal Point': 159,
 'Silver': 122,
 'Silver Lynx Point': 2,
 'Silver Tabby': 42,
 'Tan': 3025,
 'Torbie': 398,
 'Tortie': 618,
 'Tortie Point': 34,
 'Tricolor': 912,
 'White': 12186,
 'Yellow': 

In [12]:
color_cats = [x.split('/') for x in train_data['Color']]

## Feature Exploration

In [13]:
def convert_multi_cat_dummy(vals, pref, sep):
    dummies = {}
    df = pd.DataFrame(vals)
    cols = df.columns
    dummies = pd.get_dummies(df[cols[0]], columns = [cols[0]], prefix_sep=sep, prefix=pref)
    
    if len(cols) > 1:
        for c in cols[1:]:
            new_dummies = pd.get_dummies(df[c], columns = [c], prefix_sep=sep, prefix=pref)
            for x in new_dummies.columns:
                try:
                    v = dummies[x].copy()
                    dummies[x] = v + new_dummies[x]
                except:
                    dummies[x] = new_dummies[x]
                    
    return dummies

In [16]:
# First we create the feature set using one-hot encoding for the categorical features
all_feats = train_data.loc[:, ['Name', 'DateTime', 'AgeuponOutcome']]
all_feats.index = range(all_feats.shape[0])
all_feats['DateTime'] = times
all_feats['AgeuponOutcome'] = ages
all_feats['AnimalType'] = train_data['AnimalType'].astype('category').cat.codes

all_feats['Sex'] = pd.Series(sex).astype('category')
all_feats['IsFixed'] = pd.Series(is_fixed).astype('category')

all_feats['OutcomeType'] = train_data['OutcomeType'].copy().astype('category')
all_feats['OutcomeSubtype'] = train_data['OutcomeSubtype'].copy().astype('category')

color_dummies = convert_multi_cat_dummy(color_cats, 'cl', '_')
breed_dummies = convert_multi_cat_dummy(breed_cats, '', '')

color_cols = list(color_dummies.columns)
breed_cols = list(breed_dummies.columns)
otsub_cols = list(all_feats['OutcomeSubtype'].cat.categories)
at_keys = dict(zip(range(2), train_data['AnimalType'].astype('category').cat.categories))

In [17]:
all_feats = pd.get_dummies(all_feats, columns=['OutcomeSubtype'], prefix = '', prefix_sep = '')
all_feats = pd.concat([all_feats, color_dummies, breed_dummies], 1)

In [18]:
# Inpute missing age values as most common value
from sklearn.preprocessing import Imputer

im = Imputer(strategy = 'most_frequent')
all_feats['AgeuponOutcome'] = Imputer(strategy = 'most_frequent').fit_transform(all_feats.loc[:, ['AgeuponOutcome']])
all_feats['Sex'] = Imputer(strategy = 'most_frequent').fit_transform(all_feats.loc[:, ['Sex']])
all_feats['IsFixed'] = Imputer(strategy = 'most_frequent').fit_transform(all_feats.loc[:, ['IsFixed']])

In [28]:
all_feats.shape

(26729, 306)

In [69]:
all_feats.head()

Name            DateTime  AgeuponOutcome  AnimalType    Sex IsFixed  \
0  Hambone 2014-02-12 18:22:00        365.0000           1 0.0000  1.0000   
1    Emily 2013-10-13 12:44:00        365.0000           0 1.0000  1.0000   
2   Pearce 2015-01-31 12:28:00        730.0000           1 0.0000  1.0000   
3      NaN 2014-07-11 19:09:00          3.0000           0 0.0000  0.0000   
4      NaN 2013-11-15 12:52:00        730.0000           1 0.0000  1.0000   

       OutcomeType  Aggressive  At Vet  Barn    ...      Whippet  \
0  Return_to_owner           0       0     0    ...            0   
1       Euthanasia           0       0     0    ...            0   
2         Adoption           0       0     0    ...            0   
3         Transfer           0       0     0    ...            0   
4         Transfer           0       0     0    ...            0   

   Wire Hair Fox Terrier  Wirehaired Pointing Griffon  Yorkshire Terrier  \
0                      0                            0                  0   
1                      0                            0                  0   
2                      0                            0                  0   
3                      0                            0                  0   
4                      0                            0                  0   

   Borzoi  Mix  Rex  Spanish Water Dog  Tan Hound  Yorkshire  
0       0    1    0                  0          0          0  
1       0    1    0                  0          0          0  
2       0    1    0                  0          0          0  
3       0    1    0                  0          0          0  
4       0    0    0                  0          0          0  

[5 rows x 306 columns]

In [19]:
month_dummies = pd.get_dummies(pd.Series([x.month for x in all_feats['DateTime']]), 
                               columns=[], prefix = 'month', prefix_sep = '_')
weekday_dummies = pd.get_dummies(pd.Series([x.weekday() for x in all_feats['DateTime']]), 
                               columns=[], prefix = 'weekday', prefix_sep = '_')
year_dummies = pd.get_dummies(pd.Series([x.year for x in all_feats['DateTime']]), 
                               columns=[], prefix = 'year', prefix_sep = '_')

all_feats = pd.concat([all_feats, month_dummies, weekday_dummies, year_dummies], 1)

In [20]:
# Split data
# Given the target in unbalanced, we'll use a stratified sampling with proportions 80-20

from sklearn.model_selection import train_test_split

split_seed = 5

df = all_feats.drop(['Name', 'OutcomeType'], 1).copy()

X_train, X_test, y_train, y_test = train_test_split(
    df, all_feats['OutcomeType'], test_size=0.2, random_state=split_seed,
    stratify = all_feats['OutcomeType'])

### Feature Plots

Below is the normalied distribution of age, divided by class. There is clearly a relation between the age and the outcome but it is likely not linear.

1. The vast majority of animals who died in the shelter were young - probably babies that were discovered or abandoned by their mother.
2. Most of the adoptions were for young animals, whith some for older animals.
3. Only older animals were returned to owner - makes sense for lost animals.
4. The ages have a pseudo continuous distribution for young animals, but becomes more categorical for older animals - which makes sense since we measure the age of babies in terms of days and weeks, but older animals in years. 

In [31]:
iplot(go.Figure(data = [go.Histogram(x = g, name = ind, histnorm='probability') for ind,g in X_train['AgeuponOutcome'].groupby(y_train)],
               layout = go.Layout(xaxis = dict(range = [0, 1000]),
                                 title = 'Distribution of Age with Outcome')))

Below is the distribution of time with outcome.

1. For all outcomes except for return to owner, there is a peak in the summer of 2015 and a smaller peak in the summer of 2014
2. Return to owner is fairly evenly distributed, except for a small peak around fall 2016.
3. There's a small peak in adoption around xmas time in 2014 and 2015, which makes sense.
4. Euthanasia drops off significantly after summer 2015 - possible due to different policies on euthanizing unwanted animals.

In [32]:
figs = [go.Figure(data = [go.Histogram(x = g, name = ind, histnorm='probability')], 
                  layout = go.Layout(title = ind)) for ind,g in X_train['DateTime'].groupby(y_train)]
fig = pm.subplot_helper_fig(3, 2, figs)
fig['layout'].update(height = 1000)
fig['layout'].update(title = 'Distribution of Date with Outcome')
iplot(fig)

Since we can't input dates directly into a model, we'll need to change this variable.

Next lets look at the same plots using month

In [99]:
figs = [go.Figure(data = [go.Histogram(x = [k.month for k in g], name = ind, histnorm='probability')], 
                  layout = go.Layout(title = ind)) for ind,g in X_train['DateTime'].groupby(y_train)]
fig = pm.subplot_helper_fig(3, 2, figs)
fig['layout'].update(height = 1000)
fig['layout'].update(title = 'Distribution of Month with Outcome')
iplot(fig)

In [95]:
figs = [go.Figure(data = [go.Histogram(x = [k.weekday() for k in g], name = ind, histnorm='probability')], 
                  layout = go.Layout(title = ind)) for ind,g in X_train['DateTime'].groupby(y_train)]
fig = pm.subplot_helper_fig(3, 2, figs)
fig['layout'].update(height = 1000)
fig['layout'].update(title = 'Distribution of Day of Week with Outcome')
iplot(fig)

In [100]:
figs = [go.Figure(data = [go.Histogram(x = [k.year for k in g], name = ind, histnorm='probability')], 
                  layout = go.Layout(title = ind)) for ind,g in X_train['DateTime'].groupby(y_train)]
fig = pm.subplot_helper_fig(3, 2, figs)
fig['layout'].update(height = 1000)
fig['layout'].update(title = 'Distribution of Year with Outcome')
iplot(fig)

In [ ]:
Judging by these plots, we can add the following features:
    1. Month
    2. Day of Week
    3. Year

The following plot shows the following:

1. About 40% of cats and 40% of dogs are adopted
2. A greater percentage of dogs are returned to owner than cats.  Possibly because cats are harder to find when they get lost and many are outdoor cats
3. A greater percentage of cats are transfered.

In [33]:
cnts = pd.crosstab(X_train['AnimalType'], y_train)
cnts.index = [at_keys[x] for x in cnts.index]
cnts = cnts.apply(lambda x: x/float(sum(x)), 1)
iplot(go.Figure(data = [go.Bar(x = cnts.columns, y = cnts.loc[x,:], name = x) for x in cnts.index],
               layout = go.Layout(title = 'Distribution of Animal Type with Outcome')))

The sex of the animals appears to have no effect on outcome.

In [34]:
cnts = pd.crosstab(X_train['Sex'], y_train)
cnts.index = ['Male', 'Female']
cnts = cnts.apply(lambda x: x/float(sum(x)), 1)
iplot(go.Figure(data = [go.Bar(x = cnts.columns, y = cnts.loc[x,:], name = x) for x in cnts.index],
               layout = go.Layout(title = 'Distribution of Sex with Outcome')))

It appears that fixed animals are much more likely to be adopted, but non-fixed animals are much more likely to be transfered. (Possibly for fixing procedure)

In [35]:
cnts = pd.crosstab(X_train['IsFixed'], y_train)
cnts.index = ['Not Fixed', 'Fixed']
cnts = cnts.apply(lambda x: x/float(sum(x)), 1)
iplot(go.Figure(data = [go.Bar(x = cnts.columns, y = cnts.loc[x,:], name = x) for x in cnts.index],
               layout = go.Layout(title = 'Distribution of Fixed Status with Outcome')))

Looking at the distribution of the most popular animal breeds, we can see most of them had the majority of animals adopted.  However, the pitbulls had more euthanasia and returning to the owner. The domestic breeds (all cats) shows a large portion transfered. So there is definitely some relationships between breed and outcome, but it heavily depends on breed and likely interacts with animal type.

In [78]:
cnts = X_train.loc[:, breed_cols].sum()
cols = list(cnts[cnts >= 500].index)
figs = []
for c in cols:
    y = y_train.loc[X_train[c] == 1]
    cnts = y.groupby(y).count()
    cnts = cnts / float(sum(cnts))
    figs.append(go.Figure(data = [go.Bar(x = cnts.index, y = cnts.values)],
                         layout = go.Layout(title = c)))
fig = pm.subplot_helper_fig(3,3, figs)
fig['layout'].update(height = 1000)
fig['layout'].update(title = 'Distribution of Most Common Breeds with Outcome')
iplot(fig)

In [90]:
cnts = X_train.loc[:, color_cols].sum()
cols = list(cnts[cnts >= 692].index)
figs = []
for c in cols:
    y = y_train.loc[X_train[c] == 1]
    cnts = y.groupby(y).count()
    cnts = cnts / float(sum(cnts))
    figs.append(go.Figure(data = [go.Bar(x = cnts.index, y = cnts.values)],
                         layout = go.Layout(title = c)))
fig = pm.subplot_helper_fig(3,3, figs)
fig['layout'].update(height = 1000)
fig['layout'].update(title = 'Distribution of Most Common Colors with Outcome')
iplot(fig)

## Modeling

All these categorical features lend well to a random forest algorithm.  Although they can have a hard time with dummy variables, since they have issues finding splits and tend to overfit we'll try it.  We'll also try logistic regression.

In [132]:
X_train.shape

(21383, 327)

In [21]:
# Drop datetime and scale

train_feats = X_train.drop('DateTime', 1)

sc = StandardScaler()
scale_train_feats = pd.DataFrame(sc.fit_transform(train_feats), columns = train_feats.columns)


In [24]:
from sklearn.linear_model import LogisticRegressionCV

lr = LogisticRegressionCV(multi_class = 'ovr', scoring = 'f1')
lr.fit(scale_train_feats, y_train)

/Users/colleensmith/anaconda2/lib/python2.7/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning:

F-score is ill-defined and being set to 0.0 due to no predicted samples.



LogisticRegressionCV(Cs=10, class_weight=None, cv=None, dual=False,
           fit_intercept=True, intercept_scaling=1.0, max_iter=100,
           multi_class='ovr', n_jobs=1, penalty='l2', random_state=None,
           refit=True, scoring='f1', solver='lbfgs', tol=0.0001, verbose=0)

In [148]:
len(train_data['AgeuponOutcome'].loc[train_data['AgeuponOutcome'].isnull()])

18

In [25]:
lr.scores_

{'Adoption': array([[0.59568546, 0.83853642, 0.84994235, 0.85313994, 0.85323219,
         0.85308683, 0.85285384, 0.85299456, 0.85299456, 0.85299456],
        [0.57797732, 0.82652717, 0.8394329 , 0.84196635, 0.84165289,
         0.84126984, 0.84160053, 0.8415138 , 0.84118328, 0.84099174],
        [0.59046283, 0.84245661, 0.85141086, 0.85257143, 0.85210002,
         0.85214834, 0.85257143, 0.85248042, 0.85248042, 0.85266765]]),
 'Died': array([[0.        , 0.46376812, 0.95049505, 0.95049505, 0.95049505,
         0.95049505, 0.91428571, 0.87272727, 0.83185841, 0.83636364],
        [0.        , 0.52777778, 0.95049505, 0.95049505, 0.95049505,
         0.93203883, 0.92307692, 0.88888889, 0.88288288, 0.82352941],
        [0.        , 0.76190476, 0.91666667, 0.91666667, 0.91666667,
         0.90721649, 0.88888889, 0.88      , 0.85436893, 0.83809524]]),
 'Euthanasia': array([[0.        , 0.99515738, 1.        , 1.        , 1.        ,
         1.        , 1.        , 0.99879663, 0.99879663, 0.

In [172]:
lr.coef_

array([[-0.80019801,  0.45046664,  0.13570574, ..., -0.00583876,
        -0.02113622,  0.01754051],
       [-0.02045472, -0.04288269, -0.0139291 , ...,  0.0121501 ,
        -0.00092462, -0.01453421],
       [ 0.15481591, -0.03559321, -0.04063338, ...,  0.01696877,
        -0.00814632, -0.03937816],
       [ 0.79023395,  0.26099824, -0.13641201, ...,  0.004958  ,
         0.0239893 , -0.02234399],
       [-0.07845203, -0.1176015 , -0.04996584, ...,  0.0112367 ,
        -0.01660902,  0.00190528]])

In [29]:
lr.C_

array([0.04641589, 0.00599484, 0.00599484, 2.7825594 , 0.00599484])

In [27]:
test_feats = X_test.drop('DateTime', 1)

scale_test_feats = pd.DataFrame(sc.transform(test_feats), columns = test_feats.columns)

In [28]:
lr.score(scale_test_feats, y_test)

0.8778526000748222

In [32]:
lr.predict(scale_test_feats)

array(['Adoption', 'Transfer', 'Adoption', ..., 'Transfer', 'Transfer',
       'Transfer'], dtype=object)

In [34]:
from sklearn.metrics import classification_report
print(classification_report(y_test, lr.predict(scale_test_feats)))

                 precision    recall  f1-score   support

       Adoption       0.81      0.91      0.86      2154
           Died       1.00      0.92      0.96        39
     Euthanasia       1.00      1.00      1.00       311
Return_to_owner       0.72      0.53      0.61       957
       Transfer       1.00      1.00      1.00      1885

    avg / total       0.87      0.88      0.87      5346



In [35]:
from sklearn.metrics import classification_report
print(classification_report(y_train, lr.predict(scale_train_feats)))

                 precision    recall  f1-score   support

       Adoption       0.81      0.91      0.86      8615
           Died       1.00      0.92      0.96       158
     Euthanasia       1.00      1.00      1.00      1244
Return_to_owner       0.72      0.52      0.61      3829
       Transfer       1.00      1.00      1.00      7537

    avg / total       0.87      0.88      0.87     21383



In [49]:
from sklearn.metrics import roc_auc_score
from sklearn.metrics import roc_curve

cats = y_test.cat.categories
roc_figs = []
for i in range(len(cats)):
    probs = lr.predict_proba(scale_test_feats)
    labs = [int(x == cats[i]) for x in y_test]
    logit_roc_auc = roc_auc_score(labs, probs[:, i])
    fpr, tpr, thresholds = roc_curve(labs, probs[:, i])
    
    roc_figs.append(go.Figure(data = [go.Scatter(x = fpr, y = tpr, name='ROC curve'),
                                     go.Scatter(x = [0, 1.0], y = [0, 1.0], 
                                                name = 'Chance', marker = dict(color='black'))],
                             layout = go.Layout(title = cats[i])))
iplot(pm.subplot_helper_fig(3, 2, roc_figs))

In [40]:
y_test.cat.categories

Index([u'Adoption', u'Died', u'Euthanasia', u'Return_to_owner', u'Transfer'], dtype='object')